# COVID-19 Status - ML Modeling

------------
### Data Vectorization

In [3]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoder, OneHotEncoderEstimator, StringIndexer, VectorAssembler
from pyspark.sql.functions import *

In [4]:
dataset = spark.table("mldata_covid19_status")
display(dataset)

Patient dataset covid19_status City Marital Race Ethnicity Gender Suffix County State Revenue Healthcare_Coverage pct_covered age_years allergy_232347008 allergy_232350006 allergy_300913006 allergy_300916003 allergy_417532002 allergy_418689008 allergy_419263009 allergy_419474003 allergy_420174000 allergy_424213003 allergy_425525006 allergy_714035009 allergy_91930004 allergy_91934008 allergy_91935009 careplan_133899007 careplan_133901003 careplan_134435003 careplan_170836005 careplan_182964004 careplan_183401008 careplan_225358003 careplan_384758001 careplan_385691007 careplan_386257007 careplan_386522008 careplan_395082007 careplan_408869004 careplan_412776001 careplan_443402002 careplan_47387005 careplan_53950000 careplan_698360004 careplan_699728000 careplan_703040004 careplan_711282006 careplan_718347000 careplan_734163000 careplan_735984001 careplan_736252007 careplan_736254008 careplan_736285004 careplan_736353004 careplan_736690008 careplan_737434004 careplan_737471002 careplan_75162002 careplan_781831000000109 careplan_869761000000107 careplan_91251008 condition_10509002 condition_109838007 condition_110030002 condition_11218009 condition_124171000119105 condition_126906006 condition_127013003 condition_127295002 condition_128613002 condition_1501000119109 condition_1551000119108 condition_156073000 condition_157141000119108 condition_15724005 condition_15777000 condition_16114001 condition_161621004 condition_161622006 condition_162573006 condition_162864005 condition_1734006 condition_185086009 condition_190905008 condition_19169002 condition_192127007 condition_195662009 condition_195967001 condition_196416002 condition_197927001 condition_198992004 condition_200936003 condition_201834006 condition_206523001 condition_22298006 condition_225444004 condition_230265002 condition_230690007 condition_232353008 condition_233604007 condition_233678006 condition_235919008 condition_236077008 condition_237602007 condition_239720000 condition_239872002 condition_239873007 condition_24079001 condition_241929008 condition_254632001 condition_254637007 condition_254837009 condition_262574004 condition_263102004 condition_26929004 condition_271737000 condition_275272006 condition_283371005 condition_283385000 condition_284549007 condition_284551006 condition_287185009 condition_301011002 condition_302870006 condition_307731004 condition_30832001 condition_314994000 condition_33737001 condition_359817006 condition_35999006 condition_363406005 condition_367498001 condition_368581000119106 condition_36923009 condition_36971009 condition_370143000 condition_370247008 condition_38822007 condition_398254007 condition_39848009 condition_399211009 condition_40055000 condition_40275004 condition_403190006 condition_403191005 condition_403192003 condition_406602003 condition_408512008 condition_410429000 condition_422034002 condition_424132000 condition_425048006 condition_427089005 condition_428251008 condition_429007001 condition_429280009 condition_431855005 condition_431856006 condition_433144002 condition_43878008 condition_44054006 condition_443165006 condition_444448004 condition_444470001 condition_44465007 condition_444814009 condition_446096008 condition_448417001 condition_448813005 condition_449868002 condition_45816000 condition_47200007 condition_47505003 condition_47693006 condition_48333001 condition_49436004 condition_53741008 condition_55680006 condition_55822004 condition_5602001 condition_58150001 condition_59621000 condition_6072007 condition_60951000119105 condition_62106007 condition_62564004 condition_64859006 condition_65275009 condition_65363002 condition_65710008 condition_65966004 condition_67811000119102 condition_68496003 condition_698423002 condition_698754002 condition_69896004 condition_703151001 condition_70704007 condition_707577004 condition_713197008 condition_7200002 condition_72892002 condition_74400008 condition_75498004 condition_79586000 condition_80394007 condition_82423001 condition_83664006 condi

In [5]:
label = "covid19_status"
allColumns = dataset.columns

categoricalColumns = [
  "City",
  "Marital",
  "Race",
  "Ethnicity",
  "Gender",
  "Suffix",
  "County",
#   "State",
  "smoker_status"
]

# numericalColumns = ["num1",
#                     "num2"]

ignoreColumns = ["Patient", "dataset", "State", label]

numericalColumns = list(set(allColumns) - set(categoricalColumns) - set(ignoreColumns))
# print(numericalColumns)

categoricalColumnsclassVec = [c + "classVec" for c in categoricalColumns]

stages = []

In [6]:
for categoricalColumn in categoricalColumns:
  print(categoricalColumn)
  ## Category Indexing with StringIndexer
  stringIndexer = StringIndexer(inputCol=categoricalColumn, outputCol = categoricalColumn+"Index").setHandleInvalid("skip")
  ## Use OneHotEncoder to convert categorical variables into binary SparseVectors
  encoder = OneHotEncoder(inputCol=categoricalColumn+"Index", outputCol=categoricalColumn+"classVec")
  ## Add stages
  stages += [stringIndexer, encoder]

City
Marital
Race
Ethnicity
Gender
Suffix
County
smoker_status

In [7]:
## Convert label into label indices using the StringIndexer
label_stringIndexer = StringIndexer(inputCol = label, outputCol = "label", stringOrderType="alphabetAsc").setHandleInvalid("keep")
stages += [label_stringIndexer]

In [8]:
assemblerInputs = categoricalColumnsclassVec + numericalColumns
assembler = VectorAssembler(inputCols = assemblerInputs, outputCol="features").setHandleInvalid("skip")
stages += [assembler]

In [9]:
prepPipeline = Pipeline().setStages(stages)
# pipelineModel = prepPipeline.fit(train)
pipelineModel = prepPipeline.fit(dataset)
dataset = pipelineModel.transform(dataset)

# train = pipelineModel.transform(train)
# test = pipelineModel.transform(test)

In [10]:
train = dataset.filter(col("dataset") == "train")
train = train.filter(col("covid19_status").isNotNull()).sample(False, .20, 1337)

test = dataset.filter(col("dataset") == "test")

In [11]:
display(train.select("Patient", "covid19_status", "label", "features"))

Patient covid19_status label features 0170e255-75fa-4160-8d8d-4d3a3b7dbaa9 1 1.0 List(0, 1193, List(17, 356, 358, 366, 376, 423, 453, 468, 498, 505, 512, 521, 526, 545, 550, 556, 563, 564, 571, 576, 579, 595, 597, 601, 627, 637, 639, 651, 655, 681, 694, 714, 761, 765, 809, 810, 815, 838, 875, 877, 887, 888, 890, 913, 922, 934, 937, 959, 962, 965, 971, 975, 982, 1040, 1045, 1059, 1074, 1091, 1104, 1135, 1155, 1173, 1176, 1180), List(1.0, 1.0, 1.0, 1.0, 1.0, 0.0063059923990430545, 0.09, 18.0, 0.31, 0.028911420717952063, 0.06, 0.07557340278415407, 0.10276546089803718, 1.0, 0.11723124987022318, 0.0489374465669969, 0.14, 567845.15, 0.001, 1.0, 0.8998225485476999, 0.06166532242398385, 0.06166532242398385, 1.0, 1.0, 0.08, 1.0, 0.10276546089803718, 0.028911420717952063, 0.9081826122546464, 0.04, 0.14, 1.0, 0.16, 0.09181738774535364, 0.0231908213775118, 0.06166532242398385, 0.09, 1.0, 1.0, 18.0, 0.07225938085966968, 0.00491591765818551, 2.0, 4032.0, 18.0, 24.0, 1.0, 0.11723124987022318, 0.07, 0.028911420717952063, 1.0, 0.07557340278415407, 2791.48, 0.13, 0.02, 1.0, 0.17, 1.0, 1.0, 0.07557340278415407, 21.21013004791239, 0.06166532242398385, 0.43)) 040fc484-1d20-4e7e-bb49-1007be78ac54 0 0.0 List(0, 1193, List(20, 351, 353, 358, 363, 374, 379, 382, 384, 387, 393, 404, 417, 423, 431, 440, 453, 498, 505, 512, 513, 520, 521, 522, 526, 531, 539, 550, 552, 556, 563, 564, 569, 571, 575, 579, 595, 597, 607, 631, 637, 643, 650, 651, 655, 665, 666, 681, 689, 694, 714, 716, 719, 721, 722, 727, 731, 733, 746, 747, 765, 766, 767, 770, 773, 779, 780, 783, 786, 791, 794, 796, 800, 809, 810, 815, 817, 824, 826, 831, 836, 838, 842, 849, 853, 867, 869, 870, 888, 890, 891, 893, 897, 905, 911, 915, 922, 936, 946, 952, 962, 964, 965, 971, 982, 994, 997, 1003, 1009, 1031, 1036, 1040, 1043, 1044, 1045, 1047, 1049, 1051, 1053, 1055, 1056, 1057, 1059, 1060, 1067, 1071, 1078, 1084, 1088, 1089, 1091, 1099, 1100, 1101, 1109, 1110, 1116, 1125, 1133, 1135, 1140, 1141, 1151, 1155, 1161, 1173, 1176, 1180, 1181), List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 99.0, 4.0, 8.0, 76.0, 14.0, 12.0, 125.0, 0.007529677260991544, 165.0, 105.0, 0.09, 0.4, 0.02894770413865346, 0.08, 61.0, 61.0, 0.07553141281606536, 47.0, 0.102758647110112, 1.0, 66.0, 0.11715825716707505, 19.0, 0.2474756496740224, 0.13, 181147.71, 87.0, 0.001, 14.0, 0.6212234344015904, 0.06170952687314823, 0.06170952687314823, 37.0, 132.0, 0.13, 2.0, 87.0, 0.102758647110112, 0.02894770413865346, 48.0, 42.0, 0.9073308887640033, 1.0, 0.04, 0.13, 1.0, 4.0, 9.0, 132.0, 4.0, 72.0, 47.0, 125.0, 72.0, 0.18, 169.0, 99.0, 99.0, 8.0, 1.0, 71.0, 169.0, 1.0, 1.0, 47.0, 137.0, 21.0, 0.09266911123599676, 0.09066456245236924, 0.06170952687314823, 76.0, 12.0, 19.0, 8.0, 48.0, 0.1, 165.0, 19.0, 1.0, 76.0, 1.0, 72.0, 0.22141286509424624, 0.0733431849621505, 37.0, 1.0, 1.0, 105.0, 125.0, 72.0, 1762.0, 1.0, 37.0, 28.0, 0.11715825716707505, 71.0, 0.06, 0.02894770413865346, 0.07553141281606536, 1.0, 105.0, 2.0, 28.0, 137.0, 3.0, 13285.95, 4.0, 66.0, 0.13, 1.0, 1.0, 61.0, 4.0, 72.0, 48.0, 132.0, 0.02, 14.0, 137.0, 9.0, 66.0, 71.0, 12.0, 42.0, 0.18, 87.0, 9.0, 21.0, 1.0, 72.0, 1.0, 4.0, 28.0, 1.0, 21.0, 1.0, 1.0, 0.07553141281606536, 169.0, 56.50924024640657, 0.06170952687314823, 0.28, 165.0)) 0ca421db-a1bc-4df2-b90c-a8a90f937fde 0 0.0 List(0, 1193, List(5, 350, 352, 356, 358, 367, 374, 379, 382, 384, 387, 393, 399, 404, 417, 423, 426, 431, 439, 440, 442, 449, 453, 468, 481, 498, 499, 505, 512, 513, 519, 520, 521, 522, 526, 531, 536, 545, 546, 550, 552, 556, 561, 563, 564, 569, 571, 575, 579, 595, 597, 601, 610, 631, 637, 639, 640, 650, 651, 653, 655, 660, 663, 665, 669, 675, 681, 689, 694, 714, 716, 719, 721, 722, 727, 731, 733, 746, 747, 765, 766, 767, 770, 773, 780, 783, 791, 794, 795, 796, 800, 809, 810, 815, 817, 824, 826, 831, 836, 838, 842, 849, 853, 867, 869, 870, 875, 887, 888, 890, 895, 905, 910, 911, 915, 922, 931, 934, 952, 962, 964, 965, 971, 975, 982, 990, 997, 1009, 1014, 1031, 1040, 1043, 1045, 1046, 1047, 1049, 1051, 1053, 1055, 105

In [12]:
print("Number of rows in `train`: " + str(train.count()) + "\nNumber of rows in `test`: " + str(test.count()))

Number of rows in `train`: 23486
Number of rows in `test`: 29474

In [13]:
pipelineModel.write().overwrite().save("/mnt/data/ml/covid19status/pipeline")
# display(dbutils.fs.ls("/mnt/data/ml/covid19status/pipeline"))

### Logistic Regression

In [15]:
from pyspark.ml.classification import LogisticRegression
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import BinaryClassificationEvaluator
from pyspark.mllib.evaluation import BinaryClassificationMetrics

In [16]:
lr = LogisticRegression(labelCol="covid19_status", featuresCol="features")
# lr.fit(train)

In [17]:
lrparamGrid = (ParamGridBuilder()
             .addGrid(lr.regParam, [0.01, 0.1, 0.25])
             .addGrid(lr.elasticNetParam, [0.0, 0.1, 0.25])
             .addGrid(lr.maxIter, [1, 5, 10])
             .build())

In [18]:
lrevaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction", metricName = "areaUnderPR")

In [19]:
# Create 5-fold CrossValidator
lrcv = CrossValidator(estimator = lr,
                      estimatorParamMaps = lrparamGrid,
                      evaluator = lrevaluator,
                      numFolds = 3)

In [20]:
lrcvModel = lrcv.fit(train)

lrcvModel.write().overwrite().save("/mnt/data/ml/covid19status/lr")

print(lrcvModel)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.
CrossValidatorModel_55a885c1727c

In [21]:
lrpredictions = lrcvModel.transform(train)
lrpredictions_test = lrcvModel.transform(test)
# display(lrpredictions)

In [22]:
print('Accuracy:', lrevaluator.evaluate(lrpredictions))
print('AUC:', BinaryClassificationMetrics(lrpredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(lrpredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.8616442943143071
AUC: 0.9080407371341066
PR: 0.9634728538521155

### Decision Tree

In [24]:
from pyspark.ml.classification import DecisionTreeClassifier
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import BinaryClassificationEvaluator

In [25]:
dt = DecisionTreeClassifier(labelCol="label", featuresCol="features")

In [26]:
dtparamGrid = (ParamGridBuilder()
             .addGrid(dt.maxDepth, [2, 5, 10])
             .addGrid(dt.maxBins, [10, 20])
             .build())

In [27]:
dtevaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")

In [28]:
# Create 5-fold CrossValidator
dtcv = CrossValidator(estimator = dt,
                      estimatorParamMaps = dtparamGrid,
                      evaluator = dtevaluator,
                      numFolds = 3)

In [29]:
dtcvModel = dtcv.fit(train)

dtcvModel.write().overwrite().save("/mnt/data/ml/covid19status/dt")

print(dtcvModel)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.
CrossValidatorModel_b3e717cc2fc9

In [30]:
dtpredictions = dtcvModel.transform(train)
dtpredictions_test = dtcvModel.transform(test)

# display(dtpredictions)

In [31]:
print('Accuracy:', dtevaluator.evaluate(dtpredictions))
print('AUC:', BinaryClassificationMetrics(dtpredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(dtpredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.8593882113937791
AUC: 0.9251296193215842
PR: 0.9778706707706295

### Random Forest

In [33]:
from pyspark.ml.classification import RandomForestClassifier
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
from pyspark.ml.evaluation import BinaryClassificationEvaluator

In [34]:
rf = RandomForestClassifier(labelCol="label", featuresCol="features")

In [35]:
rfparamGrid = (ParamGridBuilder()
               .addGrid(rf.maxDepth, [2, 5, 10])
               .addGrid(rf.maxBins, [5, 10, 20])
               .addGrid(rf.numTrees, [5, 20, 50])
             .build())

In [36]:
rfevaluator = BinaryClassificationEvaluator(rawPredictionCol="rawPrediction")

In [37]:
# Create 5-fold CrossValidator
rfcv = CrossValidator(estimator = rf,
                      estimatorParamMaps = rfparamGrid,
                      evaluator = rfevaluator,
                      numFolds = 3)

In [38]:
rfcvModel = rfcv.fit(train)

rfcvModel.write().overwrite().save("/mnt/data/ml/covid19status/rf")

# print(rfcvModel)

MLlib will automatically track trials in MLflow. After your tuning fit() call has completed, view the MLflow UI to see logged runs.

In [39]:
rfpredictions = rfcvModel.transform(train)
rfpredictions_test = rfcvModel.transform(test)

# display(rfpredictions)

In [40]:
print('Accuracy:', rfevaluator.evaluate(rfpredictions))
print('AUC:', BinaryClassificationMetrics(rfpredictions['label','prediction'].rdd).areaUnderROC)
print('PR:', BinaryClassificationMetrics(rfpredictions['label','prediction'].rdd).areaUnderPR)

Accuracy: 0.9048936745948671
AUC: 0.9250652273383086
PR: 0.9776940465567512

In [41]:
display(dbutils.fs.ls("/mnt/data/ml/covid19status/"))

path name size dbfs:/mnt/data/ml/covid19status/dt/ dt/ 0 dbfs:/mnt/data/ml/covid19status/dtr/ dtr/ 0 dbfs:/mnt/data/ml/covid19status/lr/ lr/ 0 dbfs:/mnt/data/ml/covid19status/pipeline/ pipeline/ 0 dbfs:/mnt/data/ml/covid19status/rf/ rf/ 0

In [42]:
# # Based on: https://stackoverflow.com/questions/51831874/how-to-get-correlation-matrix-values-pyspark
# from pyspark.ml.stat import Correlation
# import pandas as pd

# def correlation_matrix(df, corr_columns, column_of_interest, method='pearson'):
#     vector_col = "corr_features"
#     assembler = VectorAssembler(inputCols=corr_columns, outputCol=vector_col)
#     df_vector = assembler.transform(df).select(vector_col)
#     matrix = Correlation.corr(df_vector, vector_col, method)

#     result = matrix.collect()[0]["pearson({})".format(vector_col)].values
#     return pd.DataFrame(result.reshape(-1, len(corr_columns)), columns=corr_columns, index=corr_columns)[column_of_interest]

  
# correlation_matrix(train, numericalColumns + ["covid19_status"], "covid19_status").sort_values(ascending=False)

In [43]:
import pandas as pd

def ExtractFeatureImportance(featureImp, dataset, featuresCol):
    list_extract = []
    for i in dataset.schema[featuresCol].metadata["ml_attr"]["attrs"]:
        list_extract = list_extract + dataset.schema[featuresCol].metadata["ml_attr"]["attrs"][i]
    varlist = pd.DataFrame(list_extract)
    varlist['score'] = varlist['idx'].apply(lambda x: featureImp[x])
    return(varlist.sort_values('score', ascending = False))
  
  
# ExtractFeatureImportance(model.stages[-1].featureImportances, dataset, "features")
dataset_fi = ExtractFeatureImportance(rfcvModel.bestModel.featureImportances, train, "features")
dataset_fi = sqlContext.createDataFrame(dataset_fi)
display(dataset_fi)

idx name score 887 QALY_Max 0.18215893141220738 545 DALY_Max 0.10518029697745956 468 QALY_Min 0.08577019070252592 934 QALY_Avg 0.06544365211575282 639 DALY_Avg 0.06055150220723356 975 QOLS_Avg 0.03970294070534787 1104 DALY_Min 0.03608513164784409 875 QOLS_Min 0.0237849398642345 1044 2708-6_Max 0.01997446832813538 615 condition_162573006 0.014798144887664713 474 medication_1736854 0.013932619456959216 786 procedure_433236007 0.012579802869968397 936 careplan_735984001 0.011987495643781336 601 QOLS_Max 0.01040909580021553 722 8480-6_Min 0.009830200755320142 847 procedure_232717009 0.009718291414456204 1166 medication_583214 0.009362145524952084 1009 39156-5_Max 0.009124017210162384 997 2069-3_Min 0.008883317072328012 666 medication_313988 0.00886481044810444 1031 2947-0_Max 0.008239242662008437 721 49765-1_Max 0.008091756699625504 824 1920-8_Max 0.007617904114441715 643 procedure_399208008 0.006905367293957879 831 33914-3_Min 0.006663238969198007 554 condition_22298006 0.006628873483699023 719 1751-7_Min 0.006312378457339434 520 2885-2_Avg 0.006103443747524713 387 29463-7_Min 0.005645808083186323 431 8302-2_Avg 0.004756876117027696 665 6768-6_Min 0.004729762340786005 908 careplan_736252007 0.004539038305374487 794 1742-6_Min 0.004414893833614951 470 procedure_40701008 0.004338691770991922 679 condition_314994000 0.004305787587942179 513 2885-2_Min 0.0040258402027843025 1125 1751-7_Avg 0.004025279632468589 460 procedure_703423002 0.003929130009117055 1189 medication_259255 0.0038889832855668457 849 6299-2_Avg 0.003874738455192829 1040 Healthcare_Coverage 0.0037612659655552757 1060 9279-1_Max 0.0037507056854369975 662 device_705643001 0.003737379000485408 575 9279-1_Min 0.0036794179612187573 856 condition_424132000 0.0035010358907126907 586 medication_705129 0.0034084956205429422 519 condition_15777000 0.003383752948904787 1086 careplan_412776001 0.003336967074296681 744 careplan_395082007 0.0029632623252272075 659 procedure_15081005 0.0028318312999189455 840 14959-1_Avg 0.0026585629775890698 740 medication_896209 0.002521558355775291 695 condition_53741008 0.0024974871171809885 1082 condition_254637007 0.0022633223288749194 1078 2708-6_Min 0.0021225688191668056 650 8867-4_Avg 0.0020883911540633482 1181 8302-2_Max 0.0020199221586045158 393 9279-1_Avg 0.002006773620425625 1173 age_years 0.0019979158118656687 1049 38483-4_Avg 0.001993704381857487 826 6299-2_Max 0.0018868120113439478 994 careplan_736353004 0.0018844747261771723 873 medication_1860480 0.0018121198997042155 552 6299-2_Min 0.0017768956944547918 539 2708-6_Avg 0.0017275172192447146 931 condition_55822004 0.0017203517017592325 685 medication_1734340 0.0014220967727690739 788 procedure_433112001 0.0013944242933709035 677 8302-2_StdDev 0.0013764480865184443 461 medication_197361 0.0013168172705180234 1003 imagingsite_51185008 0.0012192956926130867 842 8302-2_Min 0.0012120977131319214 738 1920-8_StdDev 0.001173610031651534 641 careplan_182964004 0.0011644237096591831 481 4548-4_Max 0.0011083475175463664 449 72514-3_Avg 0.0011062229176107296 859 condition_185086009 0.0010402817566222472 783 2093-3_Min 0.0010041884119539328 432 condition_233604007 0.0010008366688767079 1027 procedure_127783003 9.964070518423307E-4 952 39156-5_Avg 9.941156273974641E-4 1121 8480-6_StdDev 9.807616233271717E-4 1171 condition_237602007 9.672229054727239E-4 1055 8462-4_Max 9.652663931363204E-4 746 2571-8_Avg 9.152132402170151E-4 1135 careplan_736254008 9.126842923812569E-4 376 smoker_statusclassVec_Null 8.560727601975605E-4 564 Revenue 8.444089151917559E-4 890 pct_covered 8.430829475593574E-4 855 condition_109838007 8.153465779121022E-4 384 33914-3_Avg 7.976790724705697E-4 415 8867-4_StdDev 7.912380379327617E-4 1084 18262-6_Max 7.813502782834092E-4 1036 imagingsite_261179002 7.329264906765896E-4 820 2885-2_StdDev 7.203236474599205E-4 852 condition_87433001 7.020693899075915E-4 652 condition_126906006 6.967796440412405E-4 761 condition_370143000 6.887911669282946E-4 960 condition_703151001 6.77379114